# DM project: cheese

In [1]:
import os
import time
import json
import random

from matplotlib import colors
import matplotlib.pyplot as plt
import plotly.express as px
from geopy.geocoders import Nominatim

import tqdm.notebook as tqdm

import pandas as pd
from IPython.display import display, HTML
from mlxtend.preprocessing import TransactionEncoder
from mlxtend.frequent_patterns import apriori, association_rules

from sklearn import tree
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.linear_model import LinearRegression, Ridge, LogisticRegression, Lasso, ElasticNet, Lars

We use the following dataset from Kaggle: [Cheese: 248 different types of cheese with various characteristics](https://www.kaggle.com/datasets/joebeachcapital/cheese). 

In [2]:
data = pd.read_csv("cheeses.csv")
data

cheese                                        url   milk  \
0            Aarewasser         https://www.cheese.com/aarewasser/    cow   
1      Abbaye de Belloc   https://www.cheese.com/abbaye-de-belloc/  sheep   
2      Abbaye de Belval   https://www.cheese.com/abbaye-de-belval/    cow   
3     Abbaye de Citeaux  https://www.cheese.com/abbaye-de-citeaux/    cow   
4       Abbaye de Tamié              https://www.cheese.com/tamie/    cow   
...                 ...                                        ...    ...   
1182          Sveciaost          https://www.cheese.com/sveciaost/    cow   
1183               Swag               https://www.cheese.com/swag/   goat   
1184          Swaledale          https://www.cheese.com/swaledale/  sheep   
1185  Sweet Style Swiss  https://www.cheese.com/sweet-style-swiss/    NaN   
1186       Swiss cheese              https://www.cheese.com/swiss/    cow   

            country                      region        family  \
0       Switzerland                         NaN           NaN   
1            France                 Pays Basque           NaN   
2            France                         NaN           NaN   
3            France                    Burgundy           NaN   
4            France                      Savoie           NaN   
...             ...                         ...           ...   
1182         Sweden          Low-laying regions           NaN   
1183      Australia             South Australia           NaN   
1184        England  Swaledale, North Yorkshire           NaN   
1185    Switzerland                         NaN           NaN   
1186  United States                         NaN  Swiss Cheese   

                            type fat_content calcium_content  \
0                      semi-soft         NaN             NaN   
1             semi-hard, artisan         NaN             NaN   
2                      semi-hard      40-46%             NaN   
3     semi-soft, artisan, brined         NaN             NaN   
4                  soft, artisan         NaN             NaN   
...                          ...         ...             ...   
1182           semi-hard, brined         45%             NaN   
1183         fresh firm, artisan         NaN             NaN   
1184                        hard         NaN             NaN   
1185          semi-hard, artisan         NaN             NaN   
1186    hard, artisan, processed  7.8 g/100g             NaN   

                    texture        rind        color                 flavor  \
0                   buttery      washed       yellow                  sweet   
1       creamy, dense, firm     natural       yellow          burnt caramel   
2                   elastic      washed        ivory                    NaN   
3     creamy, dense, smooth      washed        white  acidic, milky, smooth   
4      creamy, open, smooth      washed        white          fruity, nutty   
...                     ...         ...          ...                    ...   
1182         creamy, supple    rindless  pale yellow                 acidic   
1183        creamy, crumbly  ash coated        white         acidic, creamy   
1184              semi firm         NaN       yellow          smooth, sweet   
1185           firm, supple       waxed          NaN                  nutty   
1186                   firm    rindless  pale yellow           nutty, sweet   

                  aroma vegetarian  vegan                     synonyms  \
0               buttery      False  False                          NaN   
1              lanoline       True  False  Abbaye Notre-Dame de Belloc   
2              aromatic      False  False                          NaN   
3     barnyardy, earthy      False  False                          NaN   
4     perfumed, pungent      False  False                          NaN   
...                 ...        ...    ...                          ...   
1182                NaN      False  False                          NaN   
1

## I.  Cleaning and pre-processing

In [3]:
print(len(data[pd.isnull(data["calcium_content"])]))
print(len(data[pd.isnull(data["fat_content"])]))

1162
939


Since those two columns have too much null data, we choose to remove them. 
Similarly, we removed other columns we are not interested in: 

In [4]:
unused_columns = ["alt_spellings", "producers", "calcium_content", "url", "fat_content", "synonyms"]
for col in unused_columns:
    if col in data.columns:
        del data[col]
data

cheese   milk        country                      region  \
0            Aarewasser    cow    Switzerland                         NaN   
1      Abbaye de Belloc  sheep         France                 Pays Basque   
2      Abbaye de Belval    cow         France                         NaN   
3     Abbaye de Citeaux    cow         France                    Burgundy   
4       Abbaye de Tamié    cow         France                      Savoie   
...                 ...    ...            ...                         ...   
1182          Sveciaost    cow         Sweden          Low-laying regions   
1183               Swag   goat      Australia             South Australia   
1184          Swaledale  sheep        England  Swaledale, North Yorkshire   
1185  Sweet Style Swiss    NaN    Switzerland                         NaN   
1186       Swiss cheese    cow  United States                         NaN   

            family                        type                texture  \
0              NaN                   semi-soft                buttery   
1              NaN          semi-hard, artisan    creamy, dense, firm   
2              NaN                   semi-hard                elastic   
3              NaN  semi-soft, artisan, brined  creamy, dense, smooth   
4              NaN               soft, artisan   creamy, open, smooth   
...            ...                         ...                    ...   
1182           NaN           semi-hard, brined         creamy, supple   
1183           NaN         fresh firm, artisan        creamy, crumbly   
1184           NaN                        hard              semi firm   
1185           NaN          semi-hard, artisan           firm, supple   
1186  Swiss Cheese    hard, artisan, processed                   firm   

            rind        color                 flavor              aroma  \
0         washed       yellow                  sweet            buttery   
1        natural       yellow          burnt caramel           lanoline   
2         washed        ivory                    NaN           aromatic   
3         washed        white  acidic, milky, smooth  barnyardy, earthy   
4         washed        white          fruity, nutty  perfumed, pungent   
...          ...          ...                    ...                ...   
1182    rindless  pale yellow                 acidic                NaN   
1183  ash coated        white         acidic, creamy              fresh   
1184         NaN       yellow          smooth, sweet             floral   
1185       waxed          NaN                  nutty       nutty, sweet   
1186    rindless  pale yellow           nutty, sweet                NaN   

     vegetarian  vegan  
0         False  False  
1          True  False  
2         False  False  
3         False  False  
4         False  False  
...         ...    ...  
1182      False  False  
1183       True  False  
1184       True  False  
1185      False  False  
1186       True  False  

[1187 rows x 13 columns]

Now, we are interested in having only one column representing the location for each cheese. 

In [28]:
data=data.dropna(subset=["country","region"], how="all")
data=data.fillna(value={"country":""})
data=data.fillna(value={"region":""})
print(f"{len(data)} rows remaining")
data

1140 rows remaining


cheese   milk        country                      region  \
0            Aarewasser    cow    Switzerland                               
1      Abbaye de Belloc  sheep         France                 Pays Basque   
2      Abbaye de Belval    cow         France                               
3     Abbaye de Citeaux    cow         France                    Burgundy   
4       Abbaye de Tamié    cow         France                      Savoie   
...                 ...    ...            ...                         ...   
1182          Sveciaost    cow         Sweden          Low-laying regions   
1183               Swag   goat      Australia             South Australia   
1184          Swaledale  sheep        England  Swaledale, North Yorkshire   
1185  Sweet Style Swiss    NaN    Switzerland                               
1186       Swiss cheese    cow  United States                               

            family                        type                texture  \
0              NaN                   semi-soft                buttery   
1              NaN          semi-hard, artisan    creamy, dense, firm   
2              NaN                   semi-hard                elastic   
3              NaN  semi-soft, artisan, brined  creamy, dense, smooth   
4              NaN               soft, artisan   creamy, open, smooth   
...            ...                         ...                    ...   
1182           NaN           semi-hard, brined         creamy, supple   
1183           NaN         fresh firm, artisan        creamy, crumbly   
1184           NaN                        hard              semi firm   
1185           NaN          semi-hard, artisan           firm, supple   
1186  Swiss Cheese    hard, artisan, processed                   firm   

            rind        color                 flavor              aroma  \
0         washed       yellow                  sweet            buttery   
1        natural       yellow          burnt caramel           lanoline   
2         washed        ivory                    NaN           aromatic   
3         washed        white  acidic, milky, smooth  barnyardy, earthy   
4         washed        white          fruity, nutty  perfumed, pungent   
...          ...          ...                    ...                ...   
1182    rindless  pale yellow                 acidic                NaN   
1183  ash coated        white         acidic, creamy              fresh   
1184         NaN       yellow          smooth, sweet             floral   
1185       waxed          NaN                  nutty       nutty, sweet   
1186    rindless  pale yellow           nutty, sweet                NaN   

     vegetarian  vegan                             location   latitude  \
0         False  False                        , Switzerland  46.798562   
1          True  False                  Pays Basque, France  47.686790   
2         False  False                             , France  46.603354   
3         False  False                     Burgundy, France  47.278087   
4         False  False                       Savoie, France  45.494895   
...         ...    ...                                  ...        ...   
1182      False  False           Low-laying regions, Sweden  59.674971   
1183       True  False           South Australia, Australia -30.534367   
1184       True  False  Swaledale, North Yorkshire, England  54.382993   
1185      False  False                        , Switzerland  46.798562   
1186       True  False                      , United States  39.783730   

       longitude   color_r   color_g   color_b  
0       8.231974  0.921569  0.847059  0.545098  
1       7.392763  0.921569  0.847059  0.545098  
2       1.888334  0.909804  0.784314  0.568627  
3       4.222486  0.972549  0.972549  0.972549  
4       6.384660  0.972549  0.972549  0.972549  
...          ...       ...       ...       ...  
1182   14.520858  0.952941  0.843137  0.694118  
1183  135.630121  0.972549  0.972

We removed 6 rows for which we could not find a suitable location. 

In [6]:
data.loc[data.country.str.contains("England, Great Britain, United Kingdom")|data.country.str.contains("England, United Kingdom"),"country"]="England"
data.loc[data.country.str.contains("Scotland"),"country"]="Scotland"
data.loc[data.country.str.contains("Great Britain, United Kingdom, Wales")|data.country.str.contains("United Kingdom, Wales"),"country"]="Wales"

We change some countries to get more easily the location. 

In [7]:
data=data.drop(index=data[data["country"].str.contains(",")].index)
data=data.drop(index=data[data["country"].str.contains(" and ")].index)
data.reset_index()
data

cheese   milk        country                      region  \
0            Aarewasser    cow    Switzerland                               
1      Abbaye de Belloc  sheep         France                 Pays Basque   
2      Abbaye de Belval    cow         France                               
3     Abbaye de Citeaux    cow         France                    Burgundy   
4       Abbaye de Tamié    cow         France                      Savoie   
...                 ...    ...            ...                         ...   
1182          Sveciaost    cow         Sweden          Low-laying regions   
1183               Swag   goat      Australia             South Australia   
1184          Swaledale  sheep        England  Swaledale, North Yorkshire   
1185  Sweet Style Swiss    NaN    Switzerland                               
1186       Swiss cheese    cow  United States                               

            family                        type                texture  \
0              NaN                   semi-soft                buttery   
1              NaN          semi-hard, artisan    creamy, dense, firm   
2              NaN                   semi-hard                elastic   
3              NaN  semi-soft, artisan, brined  creamy, dense, smooth   
4              NaN               soft, artisan   creamy, open, smooth   
...            ...                         ...                    ...   
1182           NaN           semi-hard, brined         creamy, supple   
1183           NaN         fresh firm, artisan        creamy, crumbly   
1184           NaN                        hard              semi firm   
1185           NaN          semi-hard, artisan           firm, supple   
1186  Swiss Cheese    hard, artisan, processed                   firm   

            rind        color                 flavor              aroma  \
0         washed       yellow                  sweet            buttery   
1        natural       yellow          burnt caramel           lanoline   
2         washed        ivory                    NaN           aromatic   
3         washed        white  acidic, milky, smooth  barnyardy, earthy   
4         washed        white          fruity, nutty  perfumed, pungent   
...          ...          ...                    ...                ...   
1182    rindless  pale yellow                 acidic                NaN   
1183  ash coated        white         acidic, creamy              fresh   
1184         NaN       yellow          smooth, sweet             floral   
1185       waxed          NaN                  nutty       nutty, sweet   
1186    rindless  pale yellow           nutty, sweet                NaN   

     vegetarian  vegan  
0         False  False  
1          True  False  
2         False  False  
3         False  False  
4         False  False  
...         ...    ...  
1182      False  False  
1183       True  False  
1184       True  False  
1185      False  False  
1186       True  False  

[1140 rows x 13 columns]

We removed 41 cheeses because they can come froms several countries. 

In [8]:
data["location"]=data["region"]+", "+data["country"]

### Converting the locations to GPS coordinates

In order to have more numeric data to apply a classification algorithm, we transform the location to GPS coordinates and the color to RGB. 

In [9]:
def str_to_gps(loc):
    l=loc.split(",")
    loc=",".join([l[0],l[-1]])# removing details gives less errors while fetching the GPS coordinates
    try:
        res=Nominatim(user_agent="dmProject").geocode(loc) 
        return (res.latitude, res.longitude)
    except AttributeError:
        loc=l[-1]
        res=Nominatim(user_agent="dmProject").geocode(loc) 
        return (res.latitude, res.longitude)
        
def get_locations(backup_file):
    errors=set()
    if os.path.isfile(backup_file):
        with open(backup_file) as f:
            return json.load(f)
    locations_to_gps = {}
    for loc in tqdm.tqdm(locs):
        time.sleep(1) # We don't want to overload the Nominatim server which will stop responding
        try:
            locations_to_gps[loc] = str_to_gps(loc)
            print(loc, locations_to_gps[loc])
        except AttributeError:
            errors.add(loc)
            print(loc, file=sys.stderr)
    with open(backup_file, "w") as f:
        json.dump(locations_to_gps, f)
    return locations_to_gps

In [10]:
locs=set(data["location"])
locations_to_gps = get_locations("locations_to_gps.json")
latitudes, longitudes = [], []
for i, value in enumerate(data.location):
    latitudes.append(locations_to_gps[value][0])
    longitudes.append(locations_to_gps[value][1])
data["latitude"] = latitudes
data["longitude"] = longitudes

In [11]:
fig = px.scatter_map(data, 
                        lat="latitude", 
                        lon="longitude", 
                        hover_name="cheese", 
                        hover_data=["cheese"],
                        color="milk",
                        zoom=1.5,
                        height=800,
                        width=1400)

fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show();

In [33]:
def filter_df(df, cols=None):
    if cols is None:
        cols = ["milk", 
                "color",
                "type", "texture", "flavor", "aroma", "family", "rind"]

    df = df.copy()
    attributes = set() # Get all the possible attributes (some are mixed in different columns)
    for col in cols:
        values = set()
        for val in set(df[col]):
            if type(val) == float: # skip NaN values
                continue
            values = values.union([x.strip().lower() for x in set(val.split(","))])
        attributes = attributes.union(values)
    row_attrs = [set() for _ in range(len(df))]  # get the attributes specific to each row
    for col in cols:
        for i, row in enumerate(df[col]):
            if type(row) != float:
                row_attrs[i] = row_attrs[i].union([x.strip().lower() for x in row.split(",")])
    for attr in attributes: # Add attributes rows
        df[attr] = list(attr in row_attrs[i] for i in range(len(df[col])))
        df=df.copy()
    for col in cols:
        del df[col]

    return df.copy()

In [34]:
data_features=filter_df(data)
data_features

cheese        country                      region vegetarian  \
0            Aarewasser    Switzerland                                  False   
1      Abbaye de Belloc         France                 Pays Basque       True   
2      Abbaye de Belval         France                                  False   
3     Abbaye de Citeaux         France                    Burgundy      False   
4       Abbaye de Tamié         France                      Savoie      False   
...                 ...            ...                         ...        ...   
1182          Sveciaost         Sweden          Low-laying regions      False   
1183               Swag      Australia             South Australia       True   
1184          Swaledale        England  Swaledale, North Yorkshire       True   
1185  Sweet Style Swiss    Switzerland                                  False   
1186       Swiss cheese  United States                                   True   

      vegan                             location   latitude   longitude  \
0     False                        , Switzerland  46.798562    8.231974   
1     False                  Pays Basque, France  47.686790    7.392763   
2     False                             , France  46.603354    1.888334   
3     False                     Burgundy, France  47.278087    4.222486   
4     False                       Savoie, France  45.494895    6.384660   
...     ...                                  ...        ...         ...   
1182  False           Low-laying regions, Sweden  59.674971   14.520858   
1183  False           South Australia, Australia -30.534367  135.630121   
1184  False  Swaledale, North Yorkshire, England  54.382993   -1.984136   
1185  False                        , Switzerland  46.798562    8.231974   
1186  False                      , United States  39.783730 -100.445882   

       color_r   color_g  ...  piquant  ash coated  cottage  cornish   feta  \
0     0.921569  0.847059  ...    False       False    False    False  False   
1     0.921569  0.847059  ...    False       False    False    False  False   
2     0.909804  0.784314  ...    False       False    False    False  False   
3     0.972549  0.972549  ...    False       False    False    False  False   
4     0.972549  0.972549  ...    False       False    False    False  False   
...        ...       ...  ...      ...         ...      ...      ...    ...   
1182  0.952941  0.843137  ...    False       False    False    False  False   
1183  0.972549  0.972549  ...    False        True    False    False  False   
1184  0.921569  0.847059  ...    False       False    False    False  False   
1185  0.000000  0.000000  ...    False       False    False    False  False   
1186  0.952941  0.843137  ...    False       False    False    False  False   

      parmesan  full-flavored  supple  processed  pleasant  
0        False          False   False      False     False  
1        False          False   False      False     False  
2        False          False   False      False     False  
3        False          False   False      False     False  
4        False          False   False      False     False  
...        ...            ...     ...        ...       ...  
1182     False          False    True      False     False  
1183     False          False   False      False     False  
1184     False          False   False      False     False  
1185     False          False    True      False     False  
1186     False          False   False       True     False  

[1140 rows x 174 columns]

Similarly, we convert the colors to their RGB representations. 

In [35]:
def color_columns(data):
    """
    Returns 3 columns corresponding to approximate RGB values of the colors on the cheeses
    """
    color_to_hex = {
        'blue': "#50564B",
        'blue-grey': "#504E4A",
        'brown': "#D19651",
        'brownish yellow': "#E5CD80",
        'cream': "#D9D9CE",
        'golden orange': "#D0915D",
        'golden yellow': "#DCBE9A",
        'green': "#6AA57F",
        'ivory': "#E8C891",
        'orange': "#C7980D",
        'pale white': "#DAD5C2",
        'pale yellow': "#F3D7B1",
        'pink and white': "#C0AB94",
        'red': "#984F18",
        'straw': "#F8EAC6",
        'white': "#F8F8F8",
        'yellow': "#EBD88B",
    }
    color_to_rgb = {color: colors.to_rgb(color_to_hex[color]) for color in color_to_hex}
    data_colors = list(color_to_rgb[color] if color in color_to_rgb else (0, 0, 0) for color in data["color"])
    return list(c[0] for c in data_colors), list(c[1] for c in data_colors), list(c[2] for c in data_colors)

In [36]:
data["color_r"], data["color_g"], data["color_b"] = color_columns(data)

In [37]:
data_features=filter_df(data)
data_features

cheese        country                      region vegetarian  \
0            Aarewasser    Switzerland                                  False   
1      Abbaye de Belloc         France                 Pays Basque       True   
2      Abbaye de Belval         France                                  False   
3     Abbaye de Citeaux         France                    Burgundy      False   
4       Abbaye de Tamié         France                      Savoie      False   
...                 ...            ...                         ...        ...   
1182          Sveciaost         Sweden          Low-laying regions      False   
1183               Swag      Australia             South Australia       True   
1184          Swaledale        England  Swaledale, North Yorkshire       True   
1185  Sweet Style Swiss    Switzerland                                  False   
1186       Swiss cheese  United States                                   True   

      vegan                             location   latitude   longitude  \
0     False                        , Switzerland  46.798562    8.231974   
1     False                  Pays Basque, France  47.686790    7.392763   
2     False                             , France  46.603354    1.888334   
3     False                     Burgundy, France  47.278087    4.222486   
4     False                       Savoie, France  45.494895    6.384660   
...     ...                                  ...        ...         ...   
1182  False           Low-laying regions, Sweden  59.674971   14.520858   
1183  False           South Australia, Australia -30.534367  135.630121   
1184  False  Swaledale, North Yorkshire, England  54.382993   -1.984136   
1185  False                        , Switzerland  46.798562    8.231974   
1186  False                      , United States  39.783730 -100.445882   

       color_r   color_g  ...  piquant  ash coated  cottage  cornish   feta  \
0     0.921569  0.847059  ...    False       False    False    False  False   
1     0.921569  0.847059  ...    False       False    False    False  False   
2     0.909804  0.784314  ...    False       False    False    False  False   
3     0.972549  0.972549  ...    False       False    False    False  False   
4     0.972549  0.972549  ...    False       False    False    False  False   
...        ...       ...  ...      ...         ...      ...      ...    ...   
1182  0.952941  0.843137  ...    False       False    False    False  False   
1183  0.972549  0.972549  ...    False        True    False    False  False   
1184  0.921569  0.847059  ...    False       False    False    False  False   
1185  0.000000  0.000000  ...    False       False    False    False  False   
1186  0.952941  0.843137  ...    False       False    False    False  False   

      parmesan  full-flavored  supple  processed  pleasant  
0        False          False   False      False     False  
1        False          False   False      False     False  
2        False          False   False      False     False  
3        False          False   False      False     False  
4        False          False   False      False     False  
...        ...            ...     ...        ...       ...  
1182     False          False    True      False     False  
1183     False          False   False      False     False  
1184     False          False   False      False     False  
1185     False          False    True      False     False  
1186     False          False   False       True     False  

[1140 rows x 174 columns]

## II. Classification

In [38]:
data_features.drop(columns=["region"])
data_features

cheese        country                      region vegetarian  \
0            Aarewasser    Switzerland                                  False   
1      Abbaye de Belloc         France                 Pays Basque       True   
2      Abbaye de Belval         France                                  False   
3     Abbaye de Citeaux         France                    Burgundy      False   
4       Abbaye de Tamié         France                      Savoie      False   
...                 ...            ...                         ...        ...   
1182          Sveciaost         Sweden          Low-laying regions      False   
1183               Swag      Australia             South Australia       True   
1184          Swaledale        England  Swaledale, North Yorkshire       True   
1185  Sweet Style Swiss    Switzerland                                  False   
1186       Swiss cheese  United States                                   True   

      vegan                             location   latitude   longitude  \
0     False                        , Switzerland  46.798562    8.231974   
1     False                  Pays Basque, France  47.686790    7.392763   
2     False                             , France  46.603354    1.888334   
3     False                     Burgundy, France  47.278087    4.222486   
4     False                       Savoie, France  45.494895    6.384660   
...     ...                                  ...        ...         ...   
1182  False           Low-laying regions, Sweden  59.674971   14.520858   
1183  False           South Australia, Australia -30.534367  135.630121   
1184  False  Swaledale, North Yorkshire, England  54.382993   -1.984136   
1185  False                        , Switzerland  46.798562    8.231974   
1186  False                      , United States  39.783730 -100.445882   

       color_r   color_g  ...  piquant  ash coated  cottage  cornish   feta  \
0     0.921569  0.847059  ...    False       False    False    False  False   
1     0.921569  0.847059  ...    False       False    False    False  False   
2     0.909804  0.784314  ...    False       False    False    False  False   
3     0.972549  0.972549  ...    False       False    False    False  False   
4     0.972549  0.972549  ...    False       False    False    False  False   
...        ...       ...  ...      ...         ...      ...      ...    ...   
1182  0.952941  0.843137  ...    False       False    False    False  False   
1183  0.972549  0.972549  ...    False        True    False    False  False   
1184  0.921569  0.847059  ...    False       False    False    False  False   
1185  0.000000  0.000000  ...    False       False    False    False  False   
1186  0.952941  0.843137  ...    False       False    False    False  False   

      parmesan  full-flavored  supple  processed  pleasant  
0        False          False   False      False     False  
1        False          False   False      False     False  
2        False          False   False      False     False  
3        False          False   False      False     False  
4        False          False   False      False     False  
...        ...            ...     ...        ...       ...  
1182     False          False    True      False     False  
1183     False          False   False      False     False  
1184     False          False   False      False     False  
1185     False          False    True      False     False  
1186     False          False   False       True     False  

[1140 rows x 174 columns]

In [39]:
Y=LabelEncoder().fit_transform(data_features["country"])
X=data_features.drop(columns=["cheese","country","region","vegetarian","location","latitude","longitude"])
data_train, data_test, target_train, target_test = train_test_split(
    X, Y)
c=tree.DecisionTreeClassifier(max_depth=4,random_state=0)
c=c.fit(data_train,target_train)
plt.figure(figsize=(150,100))
ax=plt.subplot()

tree.plot_tree(c,ax=ax,filled=True,feature_names=X.columns,);

We built a decision tree for our cheese database. 

### Linear regression: find location depending on the cheese characteristics

In [40]:
for col in ["cheese","country","region","location","vegetarian","vegan"]:
    try: 
        del data_features[col]
    except:
        pass
data_features

latitude   longitude   color_r   color_g   color_b  elastic    dry  \
0     46.798562    8.231974  0.921569  0.847059  0.545098    False  False   
1     47.686790    7.392763  0.921569  0.847059  0.545098    False  False   
2     46.603354    1.888334  0.909804  0.784314  0.568627     True  False   
3     47.278087    4.222486  0.972549  0.972549  0.972549    False  False   
4     45.494895    6.384660  0.972549  0.972549  0.972549    False  False   
...         ...         ...       ...       ...       ...      ...    ...   
1182  59.674971   14.520858  0.952941  0.843137  0.694118    False  False   
1183 -30.534367  135.630121  0.972549  0.972549  0.972549    False  False   
1184  54.382993   -1.984136  0.921569  0.847059  0.545098    False  False   
1185  46.798562    8.231974  0.000000  0.000000  0.000000    False  False   
1186  39.783730 -100.445882  0.952941  0.843137  0.694118    False  False   

      pale yellow  stringy  flaky  ...  piquant  ash coated  cottage  cornish  \
0           False    False  False  ...    False       False    False    False   
1           False    False  False  ...    False       False    False    False   
2           False    False  False  ...    False       False    False    False   
3           False    False  False  ...    False       False    False    False   
4           False    False  False  ...    False       False    False    False   
...           ...      ...    ...  ...      ...         ...      ...      ...   
1182         True    False  False  ...    False       False    False    False   
1183        False    False  False  ...    False        True    False    False   
1184        False    False  False  ...    False       False    False    False   
1185        False    False  False  ...    False       False    False    False   
1186         True    False  False  ...    False       False    False    False   

       feta  parmesan  full-flavored  supple  processed  pleasant  
0     False     False          False   False      False     False  
1     False     False          False   False      False     False  
2     False     False          False   False      False     False  
3     False     False          False   False      False     False  
4     False     False          False   False      False     False  
...     ...       ...            ...     ...        ...       ...  
1182  False     False          False    True      False     False  
1183  False     False          False   False      False     False  
1184  False     False          False   False      False     False  
1185  False     False          False    True      False     False  
1186  False     False          False   False       True     False  

[1140 rows x 168 columns]

In [41]:
X=data_features.copy()
del X["latitude"]
del X["longitude"]
y=data_features[["longitude","latitude"]]


In [42]:
for model in LinearRegression(), Ridge(), Lasso(), ElasticNet():  
    model.fit(X,y)
    print(model.score(X,y))

0.29532431752157284
0.2898301317667477
0.06917053924889166
0.036330707662109885


Not good, even quite bad. 
In short, it seems that we cannot find the region a cheese originates from given its characteristic. 

In [22]:
model.predict(X)

array([[-17.25837519,  41.83173155],
       [-18.28946977,  41.52637469],
       [-17.01544249,  41.83173155],
       ...,
       [-10.27185257,  41.83173155],
       [-19.0749781 ,  41.57789057],
       [-25.33116752,  41.48630563]], shape=(1140, 2))

In [23]:
yprime=pd.DataFrame(model.predict(X),columns=["latitude","longitude"])



## III. Pattern Mining

In [43]:
unused_columns = {"vegetarian", "vegan", "cheese", "region", "color", "location", "latitude", "longitude", "country", "color_r", "color_g", "color_b"}
data_features_only=data_features.drop(columns=list(unused_columns.intersection(data_features.columns)))
data_features_only.shape[1]

163

We have $164$ features in our data, that is very big compared to the number of rows of our data. So, we choose a min_support of $0.1$ during the apriori algorithm for pattern mining. 

In [62]:
frequent_itemsets=apriori(data_features_only,min_support=.05, use_colnames=True)
frequent_itemsets=frequent_itemsets.sort_values(by=['support'], ascending=False)
frequent_itemsets

In [66]:
assoc_rules = association_rules(frequent_itemsets, min_threshold=.5)
assoc_rules=assoc_rules.sort_values(by=['confidence'], ascending=False)
display(HTML(assoc_rules.to_html()))

In [46]:
assoc_rules[assoc_rules["consequents"].astype(str).str.contains("cow")]

antecedents    consequents  antecedent support  \
2            (pale yellow)          (cow)            0.227193   
5              (semi-hard)          (cow)            0.195614   
6                   (rich)          (cow)            0.135088   
9                (crumbly)          (cow)            0.188596   
14                 (sweet)          (cow)            0.254386   
19               (artisan)          (cow)            0.541228   
29                (creamy)          (cow)            0.560526   
37               (natural)          (cow)            0.371053   
39                 (nutty)          (cow)            0.203509   
40               (buttery)          (cow)            0.203509   
41                 (spicy)          (cow)            0.135088   
42             (semi-soft)          (cow)            0.228947   
43                  (firm)          (cow)            0.221053   
44                  (mild)          (cow)            0.198246   
45                  (hard)          (cow)            0.188596   
46                (smooth)          (cow)            0.298246   
47                  (soft)          (cow)            0.328947   
48  (artisan, pale yellow)          (cow)            0.142982   
51   (pale yellow, creamy)          (cow)            0.124561   
54       (artisan, creamy)          (cow)            0.306140   
60      (artisan, natural)          (cow)            0.238596   
62       (natural, creamy)          (cow)            0.184211   
64       (buttery, creamy)          (cow)            0.131579   
66               (buttery)  (creamy, cow)            0.203509   
67     (semi-soft, creamy)          (cow)            0.151754   
69        (creamy, smooth)          (cow)            0.193860   
71          (soft, creamy)          (cow)            0.228070   

    consequent support   support  confidence      lift  representativity  \
2             0.655263  0.178070    0.783784  1.196136               1.0   
5             0.655263  0.143860    0.735426  1.122337               1.0   
6             0.655263  0.109649    0.811688  1.238721               1.0   
9             0.655263  0.124561    0.660465  1.007939               1.0   
14            0.655263  0.160526    0.631034  0.963025               1.0   
19            0.655263  0.331579    0.612642  0.934955               1.0   
29            0.655263  0.378070    0.674491  1.029344               1.0   
37            0.655263  0.250000    0.673759  1.028226               1.0   
39            0.655263  0.142105    0.698276  1.065642               1.0   
40            0.655263  0.163158    0.801724  1.223515               1.0   
41            0.655263  0.103509    0.766234  1.169353               1.0   
42            0.655263  0.153509    0.670498  1.023250               1.0   
43            0.655263  0.143860    0.650794  0.993179               1.0   
44            0.655263  0.126316    0.637168  0.972385               1.0   
45            0.655263  0.142982    0.758140  1.157000               1.0   
46            0.655263  0.187719    0.629412  0.960548               1.0   
47            0.655263  0.200000    0.608000  0.927871               1.0   
48            0.655263  0.110526    0.773006  1.179688               1.0   
51            0.655263  0.100000    0.802817  1.225182               1.0   
54            0.655263  0.192982    0.630372  0.962014               1.0   
60            0.655263  0.151754    0.636029  0.970647               1.0   
62            0.655263  0.135088    0.733333  1.119143               1.0   
64            0.655263  0.107895    0.820000  1.251406               1.0   
66            0.378070  0.107895    0.530172  1.402312               1.0   
67            0.655263  0.104386    0.687861  1.049748               1.0   
69            0.655263  0.130702    0.674208  1.028912               1.0   
71            0.655263  0.145614    0.638462  0.974359               1.0   

    leverage  conviction  zhangs_metric   jaccard  certainty  kul

In [53]:
len(data_features[data_features["pecorino"] == True]), len(data_features[data_features["pecorino"] == False])

(38, 1102)